In [1]:
#%%
import pandas as pd
import numpy as np
from tqdm.notebook import trange, tqdm
import folium
from folium import plugins
import json

# For converting UTM to Lat Lon coords
import mgrs_to_ll

In [2]:
# Layout of the columns
layout_df = pd.read_csv('/Users/thomas.farrandibm.com/Documents/GitHub/vietnam_air_records/data/HERB/RG330.HERBO2.REVD',
                        delimiter='\t',
                        skipinitialspace=True,
                        header=None)
layout_df

0
0      650802 2 022365 06 020202 O 01000 C    13  202...
1      650802 2 022365                               ...
2      650804 2 022365 06 020202 O 00600 C    15  237...
3      650804 2 022365                               ...
4      650806 2 022365 06 020202 O 00400 C     3   42...
...                                                  ...
18082  710217 4                                      ...
18083  710217 4                                      ...
18084  710219 4        39 000000 W 00990 P     8   66...
18085  710219 4                                      ...
18086  710228 3        24 000000 B 00330 P     0   66...

[18087 rows x 1 columns]

In [3]:
def string_slicer(row, document_start_char, document_end_char):
    start_char = document_start_char - 1
    end_char = document_end_char - 1
    
    if start_char == end_char:
        sliced_string = row[start_char]
    else:
        sliced_string = row[start_char:end_char+1]
        
    return sliced_string

In [4]:
new_list = []

with tqdm(total=len(layout_df[0])) as pbar:
    for row in layout_df[0]:
        row_entry = {
            'Date of Flight': string_slicer(row, 1, 6),
            'Changed Mission Flag': string_slicer(row, 7, 7),
            'Combat Tactical Zone': string_slicer(row, 8, 8),
            'Mission Number': string_slicer(row, 10, 15),
            'Province Code': string_slicer(row, 17, 18),
            'Number of aircraft scheduled, airborne, and actually delivered': string_slicer(row, 20, 25),
            'Type of Agent': string_slicer(row, 27, 27),
            'Number of Gallons': string_slicer(row, 29, 33),
            'Type of Mission': string_slicer(row, 35, 35),
            'Flight Path Length (km)': string_slicer(row, 39, 41),
            'Area Sprayed (Hectares)': string_slicer(row, 43, 47),
            'Area Sprayed (Acres)': string_slicer(row, 49, 52),
            'Listed Area (Units unknown)': string_slicer(row, 54, 57),
            'Helicopter Abort Code': string_slicer(row, 59, 59),
            'Mission Leg Control Field': string_slicer(row, 61, 62),
            'UTM Coordinate': string_slicer(row, 64, 71),
            'Notes on original data': string_slicer(row, 73, 80)
        }
        new_list.append(row_entry)
        
df = pd.DataFrame(new_list)
df

Date of Flight Changed Mission Flag Combat Tactical Zone Mission Number  \
0             650802                                         2         022365   
1             650802                                         2         022365   
2             650804                                         2         022365   
3             650804                                         2         022365   
4             650806                                         2         022365   
...              ...                  ...                  ...            ...   
18082         710217                                         4                  
18083         710217                                         4                  
18084         710219                                         4                  
18085         710219                                         4                  
18086         710228                                         3                  

      Province Code  \
0                06   
1                     
2                06   
3                     
4                06   
...             ...   
18082                 
18083                 
18084            39   
18085                 
18086            24   

      Number of aircraft scheduled, airborne, and actually delivered  \
0                                                 020202               
1                                                                      
2                                                 020202               
3                                                                      
4                                                 020202               
...                                                  ...               
18082                                                                  
18083                                                                  
18084                                             000000               
18085                                                                  
18086                                             000000               

      Type of Agent Number of Gallons Type of Mission Flight Path Length (km)  \
0                 O             01000               C                      13   
1                                                                               
2                 O             00600               C                      15   
3                                                                               
4                 O             00400               C                       3   
...             ...               ...             ...                     ...   
18082                                                                           
18083                                                                           
18084             W             00990               P                       8   
18085                                                                           
18086             B             00330               P                       0   

      Area Sprayed (Hectares) Area Sprayed (Acres)  \
0                        202A                  499   
1                                                    
2                        237A                  585   
3                                                    
4                         42A                  103   
...                       ...                  ...   
18082                                                
18083                                                
18084                     66B                  163   
18085                                                
18086                     66B                  163   

      Listed Area (Units unknown) Helicopter Abort Code  \
0                            012{                         
1                                                         
2                            007B                         
3                                

In [5]:
df[df['Mission Number'] == '022365']

Date of Flight Changed Mission Flag Combat Tactical Zone Mission Number  \
0          650802                                         2         022365   
1          650802                                         2         022365   
2          650804                                         2         022365   
3          650804                                         2         022365   
4          650806                                         2         022365   
5          650806                                         2         022365   
10         650815                                         2         022365   
11         650815                                         2         022365   
12         650815                                         2         022365   
13         650815                                         2         022365   
16         650818                                         2         022365   
17         650818                                         2         022365   
18         650818                                         2         022365   
19         650818                                         2         022365   
72         650917                                         2         022365   
73         650919                                         2         022365   

   Province Code  \
0             06   
1                  
2             06   
3                  
4             06   
5                  
10            06   
11                 
12                 
13                 
16            06   
17                 
18                 
19                 
72            06   
73            06   

   Number of aircraft scheduled, airborne, and actually delivered  \
0                                              020202               
1                                                                   
2                                              020202               
3                                                                   
4                                              020202               
5                                                                   
10                                             020202               
11                                                                  
12                                                                  
13                                                                  
16                                             020202               
17                                                                  
18                                                                  
19                                                                  
72                                             020202               
73                                             010101               

   Type of Agent Number of Gallons Type of Mission Flight Path Length (km)  \
0              O             01000               C                      13   
1                                                                            
2              O             00600               C                      15   
3                                                                            
4              O             00400               C                       3   
5                                                                            
10             O             01300               C                       8   
11                                                                           
12                                                                           
13                                                                           
16             O             02000               C                      15   
17                                                                           
18                                                                           
19                                                                   

In [6]:
df['Type of Agent'].value_counts()

     11556
O     4103
W     1787
B      641
Name: Type of Agent, dtype: int64

In [7]:
df.columns

Index(['Date of Flight', 'Changed Mission Flag', 'Combat Tactical Zone',
       'Mission Number', 'Province Code',
       'Number of aircraft scheduled, airborne, and actually delivered',
       'Type of Agent', 'Number of Gallons', 'Type of Mission',
       'Flight Path Length (km)', 'Area Sprayed (Hectares)',
       'Area Sprayed (Acres)', 'Listed Area (Units unknown)',
       'Helicopter Abort Code', 'Mission Leg Control Field', 'UTM Coordinate',
       'Notes on original data'],
      dtype='object')

In [8]:
# Combat Tactical Zone
# Believe this refers to the combat zones which South Vietnam was split into. 
# http://www.vietnambattlefieldtours.com/tours/ctz/zones.asp
df['Combat Tactical Zone'].unique()

array(['2', '3', '1', '4'], dtype=object)

In [9]:
# Gallons of defoliant sprayed from 1965 until 1971.
gallons_series = df['Number of Gallons'].str.strip()
gallons_series[gallons_series != ''].astype(int).sum()

17621788

In [10]:
flight_length = df['Flight Path Length (km)'].str.strip()
flight_length[flight_length != ''].astype(int).sum()

86618

In [11]:
def test_vietnam_gzd_two(incomplete_utm):
    vietnam_gzd_two = '49P'
    
    full_utm = vietnam_gzd_two + incomplete_utm
    lat_lon = mgrs_to_ll.MGRStoLL(full_utm)
    lat_two = lat_lon['lat']
    lon_two = lat_lon['lon']

    if lat_two < 0:
        raise ValueError("Coordinate is being plotted in the Southern hemisphere!")
    elif lon_two < 102:
        raise ValueError("Coordinate is being plotted further East than GZD 48.")
    elif lon_two > 112:
        raise ValueError("Coordinate is being plotted further West than GZD 49")
    return lat_lon

# utm_series 
import mgrs_to_ll
lat_lon_list = []
utm_series = df['UTM Coordinate']

vietnam_gzd_one = '48P'

for incomplete_utm in utm_series:
    full_utm = vietnam_gzd_one + incomplete_utm
    lat_lon = mgrs_to_ll.MGRStoLL(full_utm)
    
    # Sense checking the values provided.
    lat = lat_lon['lat']
    lon = lat_lon['lon']
    
    if lat < 0:
        raise ValueError("Coordinate is being plotted in the Southern hemisphere!")
        
    elif lon < 102:
        lat_lon = test_vietnam_gzd_two(incomplete_utm)
            
    elif lon > 112:
        lat_lon = test_vietnam_gzd_two(incomplete_utm)
    
    elif lon > 108.7:
        lat_lon = test_vietnam_gzd_two(incomplete_utm)
        
#     except:
#         full_utm = vietnam_gzd_two + incomplete_utm
#         lat_lon = m.toLatLon(full_utm)
    lat_lon_list.append(lat_lon)
    
lat_lon_df = pd.DataFrame(lat_lon_list)
lat_lon_df

lat         lon
0      14.685235  108.112433
1      14.581959  108.160153
2      14.640486  108.145486
3      14.514566  108.188828
4      14.748270  108.482876
...          ...         ...
18082   9.395695  104.950816
18083   9.585639  104.963547
18084   9.657961  105.161337
18085   9.591021  105.178620
18086  11.591749  105.995183

[18087 rows x 2 columns]

In [12]:
fmap = folium.Map(location=[13.772205, 106.627901],
                  tiles='cartodbpositron',
                  zoom_start=5.5)
# convert to (n, 2) nd-array format for heatmap
lat_lon_array = lat_lon_df[['lat', 'lon']].values

# plot heatmap
fmap.add_child(plugins.HeatMap(lat_lon_array, radius=12))

fmap

In [13]:
df.columns

Index(['Date of Flight', 'Changed Mission Flag', 'Combat Tactical Zone',
       'Mission Number', 'Province Code',
       'Number of aircraft scheduled, airborne, and actually delivered',
       'Type of Agent', 'Number of Gallons', 'Type of Mission',
       'Flight Path Length (km)', 'Area Sprayed (Hectares)',
       'Area Sprayed (Acres)', 'Listed Area (Units unknown)',
       'Helicopter Abort Code', 'Mission Leg Control Field', 'UTM Coordinate',
       'Notes on original data'],
      dtype='object')

In [14]:
def test_vietnam_gzd_two(utm):
    vietnam_gzd_two = '49P'
    
    full_utm = vietnam_gzd_two + utm
    lat_lon = mgrs_to_ll.MGRStoLL(full_utm)
    lat_two = lat_lon['lat']
    lon_two = lat_lon['lon']

    if lat_two < 0:
        raise ValueError("Coordinate is being plotted in the Southern hemisphere!")
    elif lon_two < 102:
        raise ValueError("Coordinate is being plotted further East than GZD 48.")
    elif lon_two > 112:
        raise ValueError("Coordinate is being plotted further West than GZD 49")
    return lat_lon

    
def utm_to_lat_lon(row):
    utm = row['UTM Coordinate']
    full_utm = '48P' + utm
    lat_lon = mgrs_to_ll.MGRStoLL(full_utm)
    
    # Sense checking the values provided.
    lat = lat_lon['lat']
    lon = lat_lon['lon']
    
    if lat < 0:
        raise ValueError("Coordinate is being plotted in the Southern hemisphere!")
        
    elif lon < 102:
        lat_lon = test_vietnam_gzd_two(utm)
            
    elif lon > 112:
        lat_lon = test_vietnam_gzd_two(utm)
    
    elif lon > 108.7:
        lat_lon = test_vietnam_gzd_two(utm)
        
    return pd.Series([lat_lon['lat'], lat_lon['lon']])
        
    
df[['Lat', 'Lon']] = df.apply(utm_to_lat_lon, axis=1)

In [15]:
df

Date of Flight Changed Mission Flag Combat Tactical Zone Mission Number  \
0             650802                                         2         022365   
1             650802                                         2         022365   
2             650804                                         2         022365   
3             650804                                         2         022365   
4             650806                                         2         022365   
...              ...                  ...                  ...            ...   
18082         710217                                         4                  
18083         710217                                         4                  
18084         710219                                         4                  
18085         710219                                         4                  
18086         710228                                         3                  

      Province Code  \
0                06   
1                     
2                06   
3                     
4                06   
...             ...   
18082                 
18083                 
18084            39   
18085                 
18086            24   

      Number of aircraft scheduled, airborne, and actually delivered  \
0                                                 020202               
1                                                                      
2                                                 020202               
3                                                                      
4                                                 020202               
...                                                  ...               
18082                                                                  
18083                                                                  
18084                                             000000               
18085                                                                  
18086                                             000000               

      Type of Agent Number of Gallons Type of Mission Flight Path Length (km)  \
0                 O             01000               C                      13   
1                                                                               
2                 O             00600               C                      15   
3                                                                               
4                 O             00400               C                       3   
...             ...               ...             ...                     ...   
18082                                                                           
18083                                                                           
18084             W             00990               P                       8   
18085                                                                           
18086             B             00330               P                       0   

      Area Sprayed (Hectares) Area Sprayed (Acres)  \
0                        202A                  499   
1                                                    
2                        237A                  585   
3                                                    
4                         42A                  103   
...                       ...                  ...   
18082                                                
18083                                                
18084                     66B                  163   
18085                                                
18086                     66B                  163   

      Listed Area (Units unknown) Helicopter Abort Code  \
0                            012{                         
1                                                         
2                            007B                         
3                                

In [16]:
df[df['Date of Flight']== '710217']

Date of Flight Changed Mission Flag Combat Tactical Zone Mission Number  \
18078         710217                                         4                  
18079         710217                                         4                  
18080         710217                                         4                  
18081         710217                                         4                  
18082         710217                                         4                  
18083         710217                                         4                  

      Province Code  \
18078            42   
18079                 
18080                 
18081                 
18082                 
18083                 

      Number of aircraft scheduled, airborne, and actually delivered  \
18078                                             000000               
18079                                                                  
18080                                                                  
18081                                                                  
18082                                                                  
18083                                                                  

      Type of Agent Number of Gallons Type of Mission Flight Path Length (km)  \
18078             W             00990               P                      29   
18079                                                                           
18080                                                                           
18081                                                                           
18082                                                                           
18083                                                                           

      Area Sprayed (Hectares) Area Sprayed (Acres)  \
18078                    198B                  489   
18079                                                
18080                                                
18081                                                
18082                                                
18083                                                

      Listed Area (Units unknown) Helicopter Abort Code  \
18078                        013{                     N   
18079                                                     
18080                                                     
18081                                                     
18082                                                     
18083                                                     

      Mission Leg Control Field UTM Coordinate Notes on original data  \
18078                        1A       VR939334                          
18079                        1B       VR950403                          
18080                        2A       VR939394                          
18081                        2B       VR950399                          
18082                        3A       VR946386                          
18083                        3B       VR960596                          

            Lat         Lon  
18078  9.348661  104.944448  
18079  9.411072  104.954457  
18080  9.402930  104.944439  
18081  9.407454  104.954458  
18082  9.395695  104.950816  
18083  9.585639  104.963547

In [18]:
grouped = df.groupby(['Date of Flight', 'Mission Number'])

test_group = grouped.get_group(('710217', '      '))
test_group

Date of Flight Changed Mission Flag Combat Tactical Zone Mission Number  \
18078         710217                                         4                  
18079         710217                                         4                  
18080         710217                                         4                  
18081         710217                                         4                  
18082         710217                                         4                  
18083         710217                                         4                  

      Province Code  \
18078            42   
18079                 
18080                 
18081                 
18082                 
18083                 

      Number of aircraft scheduled, airborne, and actually delivered  \
18078                                             000000               
18079                                                                  
18080                                                                  
18081                                                                  
18082                                                                  
18083                                                                  

      Type of Agent Number of Gallons Type of Mission Flight Path Length (km)  \
18078             W             00990               P                      29   
18079                                                                           
18080                                                                           
18081                                                                           
18082                                                                           
18083                                                                           

      Area Sprayed (Hectares) Area Sprayed (Acres)  \
18078                    198B                  489   
18079                                                
18080                                                
18081                                                
18082                                                
18083                                                

      Listed Area (Units unknown) Helicopter Abort Code  \
18078                        013{                     N   
18079                                                     
18080                                                     
18081                                                     
18082                                                     
18083                                                     

      Mission Leg Control Field UTM Coordinate Notes on original data  \
18078                        1A       VR939334                          
18079                        1B       VR950403                          
18080                        2A       VR939394                          
18081                        2B       VR950399                          
18082                        3A       VR946386                          
18083                        3B       VR960596                          

            Lat         Lon  
18078  9.348661  104.944448  
18079  9.411072  104.954457  
18080  9.402930  104.944439  
18081  9.407454  104.954458  
18082  9.395695  104.950816  
18083  9.585639  104.963547

In [19]:
minh_hung_df = df[(df['Lat'] >= 13.5) & (df['Lat'] <= 14.0)]
minh_hung_df

minh_hung_grouped = minh_hung_df.groupby(['Date of Flight', 'Mission Number'])

fmap = folium.Map(location=[13.772205, 106.627901],
                  tiles='cartodbpositron',
                  zoom_start=5.5)
# convert to (n, 2) nd-array format for heatmap
for _, group in minh_hung_grouped:
    lat_lon_array = np.array([group['Lat'].values, group['Lon'].values]).T
    folium.PolyLine(lat_lon_array).add_to(fmap)

fmap 

In [20]:
minh_hung_df['Mission Leg Control Field'].value_counts()

1A    385
1B    232
2A     86
1C     62
2B     56
1D     37
3A     35
4A     25
1E     14
3B     10
2C      8
5A      6
1F      5
1G      4
6A      4
2D      3
4B      3
1H      2
2H      2
2E      2
2I      2
7A      2
2F      2
2G      2
2J      1
1I      1
Name: Mission Leg Control Field, dtype: int64

In [21]:
minh_hung_df[minh_hung_df['Mission Leg Control Field'] == '2J']

Date of Flight Changed Mission Flag Combat Tactical Zone Mission Number  \
17889         701022                                         2         021069   

      Province Code  \
17889                 

      Number of aircraft scheduled, airborne, and actually delivered  \
17889                                                                  

      Type of Agent Number of Gallons Type of Mission Flight Path Length (km)  \
17889                                                                           

      Area Sprayed (Hectares) Area Sprayed (Acres)  \
17889                                                

      Listed Area (Units unknown) Helicopter Abort Code  \
17889                                                     

      Mission Leg Control Field UTM Coordinate Notes on original data  \
17889                        2J       BR080170                          

             Lat        Lon  
17889  13.707422  108.30034

In [22]:
single_run = grouped.get_group(('701022', '021069'))
single_run

Date of Flight Changed Mission Flag Combat Tactical Zone Mission Number  \
17874         701022                                         2         021069   
17875         701022                                         2         021069   
17876         701022                                         2         021069   
17877         701022                                         2         021069   
17878         701022                                         2         021069   
17879         701022                                         2         021069   
17880         701022                                         2         021069   
17881         701022                                         2         021069   
17882         701022                                         2         021069   
17883         701022                                         2         021069   
17884         701022                                         2         021069   
17885         701022                                         2         021069   
17886         701022                                         2         021069   
17887         701022                                         2         021069   
17888         701022                                         2         021069   
17889         701022                                         2         021069   

      Province Code  \
17874            09   
17875                 
17876                 
17877                 
17878                 
17879                 
17880                 
17881                 
17882                 
17883                 
17884                 
17885                 
17886                 
17887                 
17888                 
17889                 

      Number of aircraft scheduled, airborne, and actually delivered  \
17874                                             030303               
17875                                                                  
17876                                                                  
17877                                                                  
17878                                                                  
17879                                                                  
17880                                                                  
17881                                                                  
17882                                                                  
17883                                                                  
17884                                                                  
17885                                                                  
17886                                                                  
17887                                                                  
17888                                                                  
17889                                                                  

      Type of Agent Number of Gallons Type of Mission Flight Path Length (km)  \
17874             B             02400               C                      64   
17875                                                                           
17876                                                                           
17877                                                                           
17878                                                                           
17879                                                                           
17880                                                                           
17881                                                                           
17882                                                                           
17883                                                                           
17884                                                                           
17885                                  

In [23]:


coords_list = []
for item in zip(single_run['Lon'], single_run['Lat']):
    coords_list.append(item)
coords_json = json.dumps(coords_list)
coords_json

'[[108.19925963577614, 13.661133930331335], [108.23567496210693, 13.706706824679879], [108.25415034403007, 13.706912800620692], [108.27283443978797, 13.689053566620451], [108.25467431981215, 13.661753863074408], [108.19925963577614, 13.661133930331335], [108.30034012216976, 13.70742171485753], [108.3093724102084, 13.72558682188642], [108.38418500739486, 13.645086784943569], [108.41189436446814, 13.645377304108314], [108.44009070433037, 13.600498764344806], [108.42162079927859, 13.600308141703474], [108.37514835121767, 13.626923819667217], [108.33780144550835, 13.6626605999675], [108.32846296545904, 13.671593580237163], [108.30034012216976, 13.70742171485753]]'

In [24]:
colours = [
    'red',
    'green',
    'blue',
    'yellow',
    'orange'
]

fmap = folium.Map(location=[13.772205, 106.627901],
                  tiles='cartodbpositron',
                  zoom_start=5.5)
# convert to (n, 2) nd-array format for heatmap
lat_lon_array = np.array([single_run['Lat'].values, single_run['Lon'].values]).T
for i in range(len(lat_lon_array)):
    if i == len(lat_lon_array) - 1:
        break
    else:
        folium.PolyLine([lat_lon_array[i], lat_lon_array[i+1]]).add_to(fmap)

fmap 

In [25]:
df['Lat'] >= 11.0

0         True
1         True
2         True
3         True
4         True
         ...  
18082    False
18083    False
18084    False
18085    False
18086     True
Name: Lat, Length: 18087, dtype: bool

In [26]:
len(lat_lon_array)

16

In [27]:
grouped = df.groupby(['Date of Flight', 'Mission Number'])

test_group = grouped.get_group(('710217', '      '))
test_group

Date of Flight Changed Mission Flag Combat Tactical Zone Mission Number  \
18078         710217                                         4                  
18079         710217                                         4                  
18080         710217                                         4                  
18081         710217                                         4                  
18082         710217                                         4                  
18083         710217                                         4                  

      Province Code  \
18078            42   
18079                 
18080                 
18081                 
18082                 
18083                 

      Number of aircraft scheduled, airborne, and actually delivered  \
18078                                             000000               
18079                                                                  
18080                                                                  
18081                                                                  
18082                                                                  
18083                                                                  

      Type of Agent Number of Gallons Type of Mission Flight Path Length (km)  \
18078             W             00990               P                      29   
18079                                                                           
18080                                                                           
18081                                                                           
18082                                                                           
18083                                                                           

      Area Sprayed (Hectares) Area Sprayed (Acres)  \
18078                    198B                  489   
18079                                                
18080                                                
18081                                                
18082                                                
18083                                                

      Listed Area (Units unknown) Helicopter Abort Code  \
18078                        013{                     N   
18079                                                     
18080                                                     
18081                                                     
18082                                                     
18083                                                     

      Mission Leg Control Field UTM Coordinate Notes on original data  \
18078                        1A       VR939334                          
18079                        1B       VR950403                          
18080                        2A       VR939394                          
18081                        2B       VR950399                          
18082                        3A       VR946386                          
18083                        3B       VR960596                          

            Lat         Lon  
18078  9.348661  104.944448  
18079  9.411072  104.954457  
18080  9.402930  104.944439  
18081  9.407454  104.954458  
18082  9.395695  104.950816  
18083  9.585639  104.963547

In [28]:
colours = [
    'red',
    'green',
    'blue',
    'yellow',
    'orange'
]

fmap = folium.Map(location=[13.772205, 106.627901],
                  tiles='cartodbpositron',
                  zoom_start=5.5)
# convert to (n, 2) nd-array format for heatmap
lat_lon_array = np.array([test_group['Lat'].values, test_group['Lon'].values]).T
for i in range(len(lat_lon_array)):
    if i == len(lat_lon_array) - 1:
        break
    else:
        folium.PolyLine([lat_lon_array[i], lat_lon_array[i+1]], color=colours[i]).add_to(fmap)

fmap 

In [29]:
fmap = folium.Map(location=[13.772205, 106.627901],
                  tiles='cartodbpositron',
                  zoom_start=5.5)
# convert to (n, 2) nd-array format for heatmap
for _, group in grouped:
    lat_lon_array = np.array([group['Lat'].values, group['Lon'].values]).T
    folium.PolyLine(lat_lon_array).add_to(fmap)

fmap 

In [30]:
np.array(group['Lat'], group['Lon'])

array([11.59174861])

In [31]:
[group['Lat'], group['Lon']]

[18086    11.591749
 Name: Lat, dtype: float64, 18086    105.995183
 Name: Lon, dtype: float64]

In [32]:
group

Date of Flight Changed Mission Flag Combat Tactical Zone Mission Number  \
18086         710228                                         3                  

      Province Code  \
18086            24   

      Number of aircraft scheduled, airborne, and actually delivered  \
18086                                             000000               

      Type of Agent Number of Gallons Type of Mission Flight Path Length (km)  \
18086             B             00330               P                       0   

      Area Sprayed (Hectares) Area Sprayed (Acres)  \
18086                     66B                  163   

      Listed Area (Units unknown) Helicopter Abort Code  \
18086                        002{                     N   

      Mission Leg Control Field UTM Coordinate Notes on original data  \
18086                        1A       XT085816                          

             Lat         Lon  
18086  11.591749  105.995183

In [33]:
# Monday the 7th: 701007
# Sunday the 13th: 701013
week = df[(df['Date of Flight'] == '701007') |\
          (df['Date of Flight'] == '701008') |\
          (df['Date of Flight'] == '701009') |\
          (df['Date of Flight'] == '701010') |\
          (df['Date of Flight'] == '701011') |\
          (df['Date of Flight'] == '701012') |\
          (df['Date of Flight'] == '701013')]
week

Date of Flight Changed Mission Flag Combat Tactical Zone Mission Number  \
17825         701008                    *                    2         021069   
17826         701008                                         2         021069   
17827         701008                                         2         021069   
17828         701008                                         2         021069   
17829         701008                                         2         021069   
17830         701008                                         2         021069   
17831         701008                                         2         021069   
17832         701008                                         2         021069   
17833         701008                                         2         021069   
17834         701008                                         2         021069   
17835         701008                                         2         021069   
17836         701008                                         2         021069   
17837         701008                                         2         021069   
17838         701008                                         2         021069   
17839         701009                                         1                  
17840         701009                                         1                  
17841         701010                                         1                  
17842         701010                                         1                  
17843         701010                                         1                  
17844         701010                                         1                  
17845         701010                                         2         020570   
17846         701010                                         2         020570   
17847         701010                                         2         020570   
17848         701010                                         2         020570   
17849         701010                                         2         020570   
17850         701012                                         2         020570   
17851         701012                                         2         020570   
17852         701012                                         2         020570   
17853         701012                                         2         020570   
17854         701012                                         2         020570   

      Province Code  \
17825            09   
17826                 
17827                 
17828                 
17829                 
17830                 
17831                 
17832                 
17833                 
17834                 
17835                 
17836                 
17837                 
17838                 
17839            04   
17840                 
17841            05   
17842            05   
17843            05   
17844            04   
17845            07   
17846                 
17847                 
17848                 
17849                 
17850            07   
17851                 
17852                 
17853                 
17854                 

      Number of aircraft scheduled, airborne, and actually delivered  \
17825                                             030303               
17826                                                                  
17827                                                                  
17828                                                                  
17829                                                                  
17830                                                                  
17831                                                                  
17832                                                                  
17833                                                                  
17834                                                       

In [34]:
gia_lai_df = df[df['Province Code'] == '09']
gia_lai_df

Date of Flight Changed Mission Flag Combat Tactical Zone Mission Number  \
2103          661029                                         2         200466   
2109          661030                                         2         200466   
2129          661031                                         2         200466   
2131          661101                                         2         200466   
2191          661107                                         2         200466   
2205          661108                                         2         200466   
2341          661121                    *                    2         200466   
2361          661124                                         2         200466   
2460          661205                                         2         200466   
2516          661210                                         2         200466   
2545          661213                                         2         200466   
2776          670109                                         2         200466   
5709          671003                                         2         020366   
9837          681119                                         2         021068   
9840          681119                                         2         021068   
9843          681119                                         2         021068   
16599         700214                                         2         021069   
16603         700214                                         2         021069   
17825         701008                    *                    2         021069   
17874         701022                                         2         021069   

      Province Code  \
2103             09   
2109             09   
2129             09   
2131             09   
2191             09   
2205             09   
2341             09   
2361             09   
2460             09   
2516             09   
2545             09   
2776             09   
5709             09   
9837             09   
9840             09   
9843             09   
16599            09   
16603            09   
17825            09   
17874            09   

      Number of aircraft scheduled, airborne, and actually delivered  \
2103                                              030303               
2109                                              040404               
2129                                              020202               
2131                                              030303               
2191                                              020202               
2205                                              020202               
2341                                              020202               
2361                                              020202               
2460                                              020202               
2516                                              020202               
2545                                              020202               
2776                                              030303               
5709                                              020202               
9837                                              030303               
9840                                              020202               
9843                                              020202               
16599                                             030303               
16603                                             020202               
17825                                             030303               
17874                                             030303               

      Type of Agent Number of Gallons Type of Mission Flight Path Length (km)  \
2103              W             02700               D                      10   
2109              W             03600               D                      16   
2129              W             01800               D           

In [35]:
df['Province Code'].value_counts()

      11556
21      695
19      480
02      457
07      441
06      380
24      367
01      311
12      272
23      246
26      228
29      222
08      218
10      207
05      197
03      178
42      162
04      146
18      139
15      124
27      114
22      103
34       84
17       73
11       69
13       65
35       61
40       55
25       54
43       41
16       38
38       36
36       36
28       32
93       31
41       31
33       31
31       28
09       20
32       19
39       16
46       12
14        7
30        4
44        1
Name: Province Code, dtype: int64

In [55]:
df['Province Code'].value_counts()

      11556
21      695
19      480
02      457
07      441
06      380
24      367
01      311
12      272
23      246
26      228
29      222
08      218
10      207
05      197
03      178
42      162
04      146
18      139
15      124
27      114
22      103
34       84
17       73
11       69
13       65
35       61
40       55
25       54
43       41
16       38
38       36
36       36
28       32
93       31
41       31
33       31
31       28
09       20
32       19
39       16
46       12
14        7
30        4
44        1
Name: Province Code, dtype: int64

In [38]:
gia_lai_df

Date of Flight Changed Mission Flag Combat Tactical Zone Mission Number  \
2103          661029                                         2         200466   
2109          661030                                         2         200466   
2129          661031                                         2         200466   
2131          661101                                         2         200466   
2191          661107                                         2         200466   
2205          661108                                         2         200466   
2341          661121                    *                    2         200466   
2361          661124                                         2         200466   
2460          661205                                         2         200466   
2516          661210                                         2         200466   
2545          661213                                         2         200466   
2776          670109                                         2         200466   
5709          671003                                         2         020366   
9837          681119                                         2         021068   
9840          681119                                         2         021068   
9843          681119                                         2         021068   
16599         700214                                         2         021069   
16603         700214                                         2         021069   
17825         701008                    *                    2         021069   
17874         701022                                         2         021069   

      Province Code  \
2103             09   
2109             09   
2129             09   
2131             09   
2191             09   
2205             09   
2341             09   
2361             09   
2460             09   
2516             09   
2545             09   
2776             09   
5709             09   
9837             09   
9840             09   
9843             09   
16599            09   
16603            09   
17825            09   
17874            09   

      Number of aircraft scheduled, airborne, and actually delivered  \
2103                                              030303               
2109                                              040404               
2129                                              020202               
2131                                              030303               
2191                                              020202               
2205                                              020202               
2341                                              020202               
2361                                              020202               
2460                                              020202               
2516                                              020202               
2545                                              020202               
2776                                              030303               
5709                                              020202               
9837                                              030303               
9840                                              020202               
9843                                              020202               
16599                                             030303               
16603                                             020202               
17825                                             030303               
17874                                             030303               

      Type of Agent Number of Gallons Type of Mission Flight Path Length (km)  \
2103              W             02700               D                      10   
2109              W             03600               D                      16   
2129              W             01800               D           

In [67]:
new_df = df.drop(364) # Anomalous data
grouped = new_df.groupby(['Date of Flight', 'Mission Number'])
final_json = []

for group_tuple in grouped:
    group = group_tuple[1]
    
    group_json = {
        "type": "Feature",
        "properties": {
            "date": group.iloc[0]['Date of Flight'],
            "province": int(group.iloc[0]['Province Code']),
            "mission type": group.iloc[0]['Type of Mission'],
            "flight length (km)": int(group.iloc[0]['Flight Path Length (km)']),
            "gallons": int(group.iloc[0]['Number of Gallons']),
            "acres": int(group.iloc[0]['Area Sprayed (Acres)']),
            "agent": group.iloc[0]['Type of Agent']
        },
        "geometry": {
            "type": "LineString",
            "coordinates":[
                list(item) for item in zip(group['Lon'], group['Lat'])
            ]
        }
    }
    
    final_json.append(group_json)

In [69]:
with open('meta_vietnam.json', 'w') as outfile:
    json.dump(final_json, outfile)

In [64]:
df

Date of Flight Changed Mission Flag Combat Tactical Zone Mission Number  \
0             650802                                         2         022365   
1             650802                                         2         022365   
2             650804                                         2         022365   
3             650804                                         2         022365   
4             650806                                         2         022365   
...              ...                  ...                  ...            ...   
18082         710217                                         4                  
18083         710217                                         4                  
18084         710219                                         4                  
18085         710219                                         4                  
18086         710228                                         3                  

      Province Code  \
0                06   
1                     
2                06   
3                     
4                06   
...             ...   
18082                 
18083                 
18084            39   
18085                 
18086            24   

      Number of aircraft scheduled, airborne, and actually delivered  \
0                                                 020202               
1                                                                      
2                                                 020202               
3                                                                      
4                                                 020202               
...                                                  ...               
18082                                                                  
18083                                                                  
18084                                             000000               
18085                                                                  
18086                                             000000               

      Type of Agent Number of Gallons Type of Mission Flight Path Length (km)  \
0                 O             01000               C                      13   
1                                                                               
2                 O             00600               C                      15   
3                                                                               
4                 O             00400               C                       3   
...             ...               ...             ...                     ...   
18082                                                                           
18083                                                                           
18084             W             00990               P                       8   
18085                                                                           
18086             B             00330               P                       0   

      Area Sprayed (Hectares) Area Sprayed (Acres)  \
0                        202A                  499   
1                                                    
2                        237A                  585   
3                                                    
4                         42A                  103   
...                       ...                  ...   
18082                                                
18083                                                
18084                     66B                  163   
18085                                                
18086                     66B                  163   

      Listed Area (Units unknown) Helicopter Abort Code  \
0                            012{                         
1                                                         
2                            007B                         
3                                

In [46]:
coords_list = []
for item in zip(group['Lon'], group['Lat']):
    coords_list.append(list(item))
coords_json = json.dumps(coords_list)
coords_json

'[[108.19925963577614, 13.661133930331335], [108.23567496210693, 13.706706824679879], [108.25415034403007, 13.706912800620692], [108.27283443978797, 13.689053566620451], [108.25467431981215, 13.661753863074408], [108.19925963577614, 13.661133930331335], [108.30034012216976, 13.70742171485753], [108.3093724102084, 13.72558682188642], [108.38418500739486, 13.645086784943569], [108.41189436446814, 13.645377304108314], [108.44009070433037, 13.600498764344806], [108.42162079927859, 13.600308141703474], [108.37514835121767, 13.626923819667217], [108.33780144550835, 13.6626605999675], [108.32846296545904, 13.671593580237163], [108.30034012216976, 13.70742171485753]]'

In [47]:
coords_list

[[108.19925963577614, 13.661133930331335],
 [108.23567496210693, 13.706706824679879],
 [108.25415034403007, 13.706912800620692],
 [108.27283443978797, 13.689053566620451],
 [108.25467431981215, 13.661753863074408],
 [108.19925963577614, 13.661133930331335],
 [108.30034012216976, 13.70742171485753],
 [108.3093724102084, 13.72558682188642],
 [108.38418500739486, 13.645086784943569],
 [108.41189436446814, 13.645377304108314],
 [108.44009070433037, 13.600498764344806],
 [108.42162079927859, 13.600308141703474],
 [108.37514835121767, 13.626923819667217],
 [108.33780144550835, 13.6626605999675],
 [108.32846296545904, 13.671593580237163],
 [108.30034012216976, 13.70742171485753]]

In [48]:
df['Number of aircraft scheduled, airborne, and actually delivered'].str[-2:].value_counts()

      11556
03     2415
00     1296
02     1036
04      594
06      497
05      327
01      149
07       77
08       77
09       53
12        7
11        2
10        1
Name: Number of aircraft scheduled, airborne, and actually delivered, dtype: int64